In [2]:
import pandas as pd
import torch
import torch.nn as nn
import torch.optim as optim
import numpy as np
from transformers import BertTokenizer
from torch.utils.data import Dataset, DataLoader
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report

import torch
from torch.utils.data import Dataset, DataLoader
import torch.nn as nn
import torch.nn.functional as F
from torch.nn.utils.rnn import pad_sequence
import torch.optim as optim

/Users/hebup/Documents/Causal Inference/cinf/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


# Load Dataset

In [25]:
df = pd.read_csv("hf://datasets/owaiskha9654/PubMed_MultiLabel_Text_Classification_Dataset_MeSH/PubMed Multi Label Text Classification Dataset Processed.csv")
df = df.sample(n=10000, random_state=42) # for testing purposes

In [26]:
df.head()

Title  \
33553  Vertical trauma: injuries to patients who fall...   
9427   The influence of bilateral sagittal split ramu...   
199    Altered metabolic incorporation of fucose and ...   
12447  Higher temperatures increase developmental rat...   
39489  MR imaging of the flexed knee: comparison to t...   

                                            abstractText  \
33553  We reviewed the patterns of injuries sustained...   
9427   The effect of orthodontic-surgical treatment o...   
199    Sciatic nerves of 25-week-old genetically diab...   
12447  Effects of temperature on development of Raja ...   
39489  The aim of this study was to obtain MR images ...   

                                               meshMajor      pmid  \
33553  ['Accidental Falls', 'Accidents', 'Adolescent'...   2916780   
9427   ['Adolescent', 'Adult', 'Chin', 'Esthetics, De...  24946129   
199    ['Animals', 'Carbon Radioisotopes', 'Diabetes ...   6888648   
12447  ['Adaptation, Biological', 'Analysis of Varian...  31049955   
39489  ['Adolescent', 'Adult', 'Arthroscopy', 'Female...  11097414   

                                                  meshid  \
33553  [['N06.850.135.122'], ['N06.850.135'], ['M01.0...   
9427   [['M01.060.057'], ['M01.060.116'], ['A01.456.5...   
199    [['B01.050'], ['D01.268.150.075.328', 'D01.496...   
12447  [['G16.012'], ['E05.318.740.150', 'N05.715.360...   
39489  [['M01.060.057'], ['M01.060.116'], ['E01.370.3...   

                                                meshroot  A  B  C  D  E  F  G  \
33553  ['Health Care [N]', 'Named Groups [M]', 'Organ...  0  1  1  0  0  1  0   
9427   ['Named Groups [M]', 'Anatomy [A]', 'Analytica...  1  1  0  0  1  0  0   
199    ['Organisms [B]', 'Chemicals and Drugs [D]', '...  1  1  1  1  1  0  0   
12447  ['Phenomena and Processes [G]', 'Analytical, D...  0  1  0  0  1  0  1   
39489  ['Named Groups [M]', 'Analytical, Diagnostic a...  1  1  1  0  1  0  1   

       H  I  J  L  M  N  Z  
33553  0  1  0  0  1  1  0  
9427   0  0  0  0  1  1  0  
199    0  0  0  0  0  0  0  
12447  0  0  0  0  0  1  1  
39489  0  0  0  0  1  1  0

In [27]:
old_df = df.copy()

In [28]:
df = old_df.copy()

In [29]:
categories = ['A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J', 'L', 'M', 'N', 'Z']
curU = 'A'
#remove curU from all_categories
categories.remove(curU)

#make df have only Title, abstractText, curU, and every category in categories
df = df[['Title', 'abstractText', curU] + categories]
#condense Title, abstractText into just "text"
df['text'] = df['Title'] + ' ' + df['abstractText']
df = df.drop(['Title', 'abstractText'], axis=1)
#tokenize text
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
df['text'] = df['text'].apply(lambda x: tokenizer.encode(x, add_special_tokens=True))
df.head()
#make a column "feature" that is [text, 'A', 'B', 'C', ...]
df['feature'] = df.apply(lambda x: [x['text']] + x[categories].values.tolist(), axis=1)
df = df.drop(categories, axis=1)
df = df.drop(['text'], axis=1)
#rename curU to "label"
df = df.rename(columns={curU: 'label'})
df = df.dropna()
df = df.reset_index(drop=True)
df.head()

#add validation
train_size = 0.7
val_size = 0.15

train_df = df.sample(frac=train_size, random_state=200)
remaining_df = df.drop(train_df.index)
val_df = remaining_df.sample(frac=val_size / (1 - train_size), random_state=200)
test_df = remaining_df.drop(val_df.index)

train_df = train_df.reset_index(drop=True)
val_df = val_df.reset_index(drop=True)
test_df = test_df.reset_index(drop=True)


Token indices sequence length is longer than the specified maximum sequence length for this model (749 > 512). Running this sequence through the model will result in indexing errors


# Custom Classes

In [30]:
# Custom Dataset class
class TextDataset(Dataset):
    def __init__(self, dataframe):
        self.features = dataframe['feature'].values
        self.labels = dataframe['label'].values

    def __len__(self):
        return len(self.features)

    def __getitem__(self, idx):
        full_feature = self.features[idx]
        text = torch.tensor(full_feature[0], dtype=torch.long)  # Tokenized text
        categories = torch.tensor(full_feature[1:], dtype=torch.float)  # Other categories
        label = torch.tensor(self.labels[idx], dtype=torch.float)  # Binary label
        return text, categories, label

def collate_fn(batch):
    texts, categories, labels = zip(*batch)
    texts_padded = pad_sequence(texts, batch_first=True, padding_value=0)  # Pad texts
    categories = torch.stack(categories)  # Stack category vectors
    labels = torch.stack(labels).unsqueeze(1)  # Stack labels and add dimension
    return texts_padded, categories, labels


train_dataset = TextDataset(train_df)
val_dataset = TextDataset(val_df)

train_dataloader = DataLoader(train_dataset, batch_size=32, shuffle=True, collate_fn=collate_fn)
val_dataloader = DataLoader(val_dataset, batch_size=32, shuffle=False, collate_fn=collate_fn)

In [47]:
class TextCNN(nn.Module):
    def __init__(self, vocab_size, embedding_dim, num_filters, kernel_sizes, dense_dim, category_dim, pretrained_embeddings=None):
        super(TextCNN, self).__init__()

        self.embedding = nn.Embedding(vocab_size, embedding_dim) if pretrained_embeddings is None else nn.Embedding.from_pretrained(pretrained_embeddings, freeze=False)
        self.embedding_dropout = nn.Dropout(0.3)

        self.convs = nn.ModuleList([
            nn.Sequential(
                nn.Conv1d(in_channels=embedding_dim, out_channels=num_filters, kernel_size=k, padding='same'),
                nn.BatchNorm1d(num_filters),
                nn.LeakyReLU(),
                nn.Dropout(0.4)
            )
            for k in kernel_sizes
        ])

        self.category_fc = nn.Linear(category_dim, dense_dim)
        self.fc1 = nn.Linear(num_filters * len(kernel_sizes) + dense_dim, dense_dim)
        self.fc2 = nn.Linear(dense_dim, 1)
        self.dropout = nn.Dropout(0.6)
        self.sigmoid = nn.Sigmoid()

    def forward(self, text, categories):
        embedded = self.embedding_dropout(self.embedding(text)).permute(0, 2, 1)
        conv_outs = [conv(embedded).max(dim=2)[0] for conv in self.convs]
        text_features = torch.cat(conv_outs, dim=1)

        category_features = F.leaky_relu(self.category_fc(categories))

        combined_features = torch.cat([text_features, category_features], dim=1)
        combined_features = self.dropout(combined_features)
        output = self.sigmoid(self.fc2(F.leaky_relu(self.fc1(combined_features))))
        return output

# Model Parameters
vocab_size = tokenizer.vocab_size
embedding_dim = 100  # Reduced from 128
num_filters = 128  # Reduced from 200
kernel_sizes = [3, 4, 5]
dense_dim = 64
epochs = 20  # Increased from 15
category_dim = len(df['feature'][0]) - 1

# Initialize model
model = TextCNN(vocab_size, embedding_dim, num_filters, kernel_sizes, dense_dim, category_dim)

# Add L2 regularization
weight_decay = 1e-5
optimizer = optim.AdamW(model.parameters(), lr=0.001, weight_decay=weight_decay)
criterion = nn.BCELoss()

# Learning rate scheduler
scheduler = optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode='min', factor=0.1, patience=3, verbose=True)

# Gradient clipping
clip_value = 1.0
torch.nn.utils.clip_grad_norm_(model.parameters(), clip_value)


/Users/hebup/Documents/Causal Inference/cinf/lib/python3.11/site-packages/torch/optim/lr_scheduler.py:62: UserWarning: The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.
  warnings.warn(


tensor(0.)

# CNN (Generating U*): ($U* | T, C_1, C_2 \dots C_n$)

In [ ]:
import matplotlib.pyplot as plt

def train_model(model, train_dataloader, val_dataloader, criterion, optimizer, epochs=15):
    train_losses, val_losses = [], []
    train_accuracies, val_accuracies = [], []

    for epoch in range(epochs):
        # Training
        model.train()
        total_train_loss = 0
        train_correct = 0
        total_samples = 0

        for texts, categories, labels in train_dataloader:
            optimizer.zero_grad()
            outputs = model(texts, categories)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()
            total_train_loss += loss.item()

            # Calculate accuracy
            preds = (outputs >= 0.5).float()
            train_correct += (preds == labels).sum().item()
            total_samples += labels.size(0)

        avg_train_loss = total_train_loss / len(train_dataloader)
        train_accuracy = train_correct / total_samples
        train_losses.append(avg_train_loss)
        train_accuracies.append(train_accuracy)

        # Validation
        model.eval()
        total_val_loss = 0
        val_correct = 0
        total_val_samples = 0

        with torch.no_grad():
            for texts, categories, labels in val_dataloader:
                outputs = model(texts, categories)
                loss = criterion(outputs, labels)
                total_val_loss += loss.item()

                # Calculate validation accuracy
                preds = (outputs >= 0.5).float()
                val_correct += (preds == labels).sum().item()
                total_val_samples += labels.size(0)

        avg_val_loss = total_val_loss / len(val_dataloader)
        val_accuracy = val_correct / total_val_samples
        val_losses.append(avg_val_loss)
        val_accuracies.append(val_accuracy)

        # Print epoch results
        print(f"Epoch {epoch + 1}, Train Loss: {avg_train_loss:.4f}, Val Loss: {avg_val_loss:.4f}, Train Acc: {train_accuracy:.4f}, Val Acc: {val_accuracy:.4f}")

    return train_losses, val_losses, train_accuracies, val_accuracies

epochs = 15

# Train the model and get stats
train_losses, val_losses, train_accuracies, val_accuracies = train_model(
    model, train_dataloader, val_dataloader, criterion, optimizer, epochs=epochs
)

# Plot Losses
plt.figure(figsize=(10, 5))
plt.plot(train_losses, label='Training Loss')
plt.plot(val_losses, label='Validation Loss')
plt.xlabel('Epochs')
plt.ylabel('Loss')
plt.title('Training and Validation Loss')
plt.legend()
plt.show()

# Plot Accuracies
plt.figure(figsize=(10, 5))
plt.plot(train_accuracies, label='Training Accuracy')
plt.plot(val_accuracies, label='Validation Accuracy')
plt.xlabel('Epochs')
plt.ylabel('Accuracy')
plt.title('Training and Validation Accuracy')
plt.legend()
plt.show()


Epoch 1, Train Loss: 0.7073, Val Loss: 0.6797, Train Acc: 0.5319, Val Acc: 0.5527


In [ ]:
# save the model
import torch

# Assuming 'model' is your trained model
torch.save(model.state_dict(), '15ep72acc.pth')

# To download the saved model file:
from google.colab import files
files.download('15ep72acc.pth')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# Load/Test

In [32]:
#open model.pth
model = TextCNN(vocab_size, embedding_dim, num_filters, kernel_sizes, dense_dim, category_dim)
model.load_state_dict(torch.load('cur_model.pth'))
model.eval()

/var/folders/rn/tyctv41n25qbtzwz02xs0fy80000gn/T/ipykernel_62463/994276552.py:3: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  model.load_state_dict(torch.load('cur_model.pt

TextCNN(
  (embedding): Embedding(30522, 100)
  (embedding_dropout): Dropout(p=0.3, inplace=False)
  (convs): ModuleList(
    (0): Sequential(
      (0): Conv1d(100, 128, kernel_size=(3,), stride=(1,), padding=same)
      (1): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): LeakyReLU(negative_slope=0.01)
      (3): Dropout(p=0.4, inplace=False)
    )
    (1): Sequential(
      (0): Conv1d(100, 128, kernel_size=(4,), stride=(1,), padding=same)
      (1): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): LeakyReLU(negative_slope=0.01)
      (3): Dropout(p=0.4, inplace=False)
    )
    (2): Sequential(
      (0): Conv1d(100, 128, kernel_size=(5,), stride=(1,), padding=same)
      (1): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): LeakyReLU(negative_slope=0.01)
      (3): Dropout(p=0.4, inplace=False)
    )
  )
  (category_fc): Linear(in_features=13, out_featu

In [33]:
# Function to evaluate on a test set and get confidence scores
def evaluate_on_test(model, test_dataloader):
    model.eval()
    all_preds = []
    all_labels = []
    all_confidences = []

    with torch.no_grad():
        for texts, categories, labels in test_dataloader:
            outputs = model(texts, categories)
            preds = (outputs >= 0.5).float()
            confidence_scores = outputs.squeeze().tolist()  # Convert to list

            all_preds.extend(preds.squeeze().tolist())
            all_labels.extend(labels.squeeze().tolist())
            all_confidences.extend(confidence_scores)

    # Calculate accuracy
    accuracy = accuracy_score(all_labels, all_preds)
    print(f"Test Accuracy: {accuracy:.4f}")

    return all_preds, all_labels, all_confidences

# Create test DataLoader
test_dataset = TextDataset(test_df)
test_dataloader = DataLoader(test_dataset, batch_size=32, shuffle=False, collate_fn=collate_fn)

# Evaluate on test set
preds, labels, confidences = evaluate_on_test(model, test_dataloader)


Test Accuracy: 0.7247


# Reconstructing U from B using RandomForest: $B \rightarrow (U* == U)$

In [34]:
#display preds
print(preds)

#shape
print(len(preds))


#show test dataset columns, size, head
print(test_df.columns)
print(test_df.shape)
print(test_df.head())

#first data point, 
print(test_df['feature'][0][1:])

[1.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, 1.0, 1.0, 0.0, 1.0, 0.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 1.0, 0.0, 1.0, 1.0, 1.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0, 1.0, 0.0, 0.0, 1.0, 1.0, 0.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 0.0, 1.0, 1.0, 1.0, 0.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.0, 1.0, 1.0, 1.0, 0.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 1.0, 1.0, 0.0, 1.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0,

In [40]:
#our current label is 'U', our preds is 'U*'
#let 'B' be 0 if 'U != U*', 1 if 'U == U*'

#error_rate set should have features of U, A, B ... Z, text
#and label of B

error_rate = test_df.copy()
#add a new column 'B' to error_rate
error_rate['B'] = (error_rate['label'] == preds).astype(int)
#add each pred value to the end of each respective feature
for i in range(len(error_rate)):
    error_rate['feature'][i].append(preds[i])

#drop all columns except 'feature' and 'B'
error_rate = error_rate.drop(['label'], axis=1)

#rename 'B' to 'label'
error_rate = error_rate.rename(columns={'B': 'label'})



'''try doing this without the text'''
#remove the first element of each feature
for i in range(len(error_rate)):
    error_rate['feature'][i] = error_rate['feature'][i][1:]
#make them all int
for i in range(len(error_rate)):
    error_rate['feature'][i] = [int(x) for x in error_rate['feature'][i]]

print(error_rate.head())


print(error_rate.shape)

                                            feature  label
0  [1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1]      1
1  [1, 0, 1, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0]      0
2  [1, 1, 0, 1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 0, 0, 0]      1
3  [1, 0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1]      1
4  [1, 1, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1]      1
(1500, 2)


/var/folders/rn/tyctv41n25qbtzwz02xs0fy80000gn/T/ipykernel_62463/3499218115.py:25: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  error_rate['feature'][i] = error_rate['feature'][i][1:]
/var/folders/rn/tyctv41n25qbtzwz02xs0fy80000gn/T/ipykern

In [41]:
#randomforest to classify label based on features in error_rate

from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report

# Split into train and test sets
train_size = 0.8
train_error_rate = error_rate.sample(frac=train_size, random_state=200)
test_error_rate = error_rate.drop(train_error_rate.index)

clf = RandomForestClassifier(n_estimators=100, random_state=42)
clf.fit(list(train_error_rate['feature']), train_error_rate['label'])

# Predict on test set
err_preds = clf.predict(list(test_error_rate['feature']))
accuracy = accuracy_score(test_error_rate['label'], err_preds)
print(f"Test Accuracy: {accuracy:.4f}")

# Classification report
print(classification_report(test_error_rate['label'], err_preds))




Test Accuracy: 0.6767
              precision    recall  f1-score   support

           0       0.37      0.19      0.25        86
           1       0.73      0.87      0.79       214

    accuracy                           0.68       300
   macro avg       0.55      0.53      0.52       300
weighted avg       0.63      0.68      0.64       300

